In [2]:
import pandas as pd
import numpy as np
from langdetect import detect
import re

In [3]:
comments1 = pd.read_excel('../data/2_5242423354782122371.xlsx')

In [4]:
comments2 = pd.read_excel('../data/2_5242423354782122372.xlsx')

In [5]:
comments2.head()

Platform        Country        Date     App ID      App Name  Publisher ID  \
0      iOS  United States  02/27/2018  640111933  Pixel Gun 3D     561634640   
1      iOS  United States  02/27/2018  640111933  Pixel Gun 3D     561634640   
2      iOS  United States  02/27/2018  640111933  Pixel Gun 3D     561634640   
3      iOS  United States  02/27/2018  640111933  Pixel Gun 3D     561634640   
4      iOS  United States  02/27/2018  640111933  Pixel Gun 3D     561634640   

  Publisher Name           User Version  Rating          Title  \
0    Cubic Games     lukieboy54  13.5.3       5  So awesome!!!   
1    Cubic Games    BeastyTwin7  13.5.3       5   Amazing Game   
2    Cubic Games  Ymartinez1748  13.5.3       5      Good game   
3    Cubic Games     savaga tbh  13.5.3       5       Best app   
4    Cubic Games       recethan  13.5.3       5     Suggestion   

                                              Review  
0  This is the most fun app i ever played but has...  
1  Why is it so hard to get a mythical pet from b...  
2  Ti is a fun game to play the have cool weapons...  
3         Is a great app and everyone should get it.  
4  I love this game and I play it all the time an...

In [6]:
comments = pd.concat([comments1[['Rating', 'Review']], comments2[['Rating', 'Review']]], axis = 0)

In [ ]:
def detect_lang(x):
    try:
        return detect(x)
    except:
        return 'unknown'
comments['lang'] = comments.Review.apply(detect_lang)

In [ ]:
comments.lang.value_counts()

In [23]:
comments.head()

Rating                                             Review lang
0       4                               Очень хорошая игра:)   ru
1       5  Ich habe es vor 3 wochen runtergeladen war all...   de
2       5                         Me encanta y soy manucraft   es
3       4  E destul de bun jocul dar la grafica mai trebu...   ro
4       5             Bueno me gustan los juegos de pistolas   es

In [6]:
#comments.to_csv('../data/comments_lang.csv')
comments = pd.read_csv('../data/comments_lang.csv')

In [7]:
comments_en = comments[comments.lang == 'en']
n_train = 13800
comments_en_train = comments_en.iloc[:n_train,:].sample(frac = 1)
comments_en_test = comments_en.iloc[n_train:,:].sample(frac = 1)

In [22]:
import enchant
c = enchant.Dict("en_UK")
def check_spelling(text):
    if not c.check(text):
        suggestions = list(set(c.suggest(text)).intersection(set(pw)))
        if len(suggestions)>0:
            res = suggestions[0]
        else:
            res = text
    else:
        res = text
    return res

In [234]:
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import re
import nltk
from nltk.corpus import wordnet
def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return ''

def clean_comment(text):
    wnl = WordNetLemmatizer()
    #deacc = re.sub(r'\W',' ', text)
    tokens = word_tokenize(text)
    tags = nltk.pos_tag(tokens)
    processed = []
    for (word, tag) in tags:
        wn_tag = get_wordnet_pos(tag)
        if wn_tag!='':
            processed.append(wnl.lemmatize(word,wn_tag))
        else:
            processed.append(wnl.lemmatize(word))
    return ' '.join(processed)

In [235]:
clean_comment(comments_en.cleaned.iloc[0])

'I really like this game I be currently on level 38 with my friend However I catch up with them by pure control and time because they spend money on this game I often get a lot of kill by Anti hero rifle of the sniper catagory but Due to the early update it really get meddle up I win jackpot and upgrade this weapon so effortively but it s now only level 16 with 57 fire rate and 5 capacity It wa use to be one shot kill body or head It cost more than the anti champion rifle I really want some other weapon all balance naturally by stimulate precision between effort the no money spender have put on it'

In [237]:
comments_en.loc[:,'cleaned'] = comments_en.Review.apply(clean_comment)

/home/lsm/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:537: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [264]:
#comments_en_train.iloc[:1000,:].to_excel('manual_labels.xlsx')

In [269]:
#comments_en_train.iloc[1000:,:].to_excel('manual_unlabeled.xlsx')

In [3]:
comments_en = pd.read_csv('comments_en_cleaned.csv')

In [4]:
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import re
import nltk
from nltk.corpus import wordnet
from emoji.unicode_codes import UNICODE_EMOJI
import emoji
def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return ''

def clean_comment(text):
    wnl = WordNetLemmatizer()
    deacc = re.sub(r'\!',' exclamation_point ', text)
    tokens = word_tokenize(deacc)
    tags = nltk.pos_tag(tokens)
    processed = []
    for (word, tag) in tags:
        wn_tag = get_wordnet_pos(tag)
        if wn_tag!='':
            processed.append(wnl.lemmatize(word,wn_tag))
        else:
            processed.append(wnl.lemmatize(check_spelling(word)))
    res = ' '.join(processed)
    return res

In [5]:
from __future__ import print_function
from time import time

from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation

In [13]:
n_samples = len(comments_en_train)
n_features = 1000
n_components = 10
n_top_words = 50

def store_top_words(model, feature_names, n_top_words):
    msg = []
    for topic_idx, topic in enumerate(model.components_):
        #message = "Topic #%d: " % topic_idx
        message = " ".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        msg.append(message)
    res = pd.Series(msg)
    res.to_excel('lda_topics.xls')

    
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += "' '".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)
    print()
print("Extracting tf features for LDA...")

tf_vectorizer = CountVectorizer(max_df=0.95, min_df=2,
                                ngram_range = (1,3),
                                max_features=n_features,
                                stop_words='english')
t0 = time()
tf = tf_vectorizer.fit_transform(comments_en_train.Review)
print("done in %0.3fs." % (time() - t0))
print("Fitting LDA models with tf features, "
      "n_samples=%d and n_features=%d..."
      % (n_samples, n_features))
lda = LatentDirichletAllocation(n_components=n_components, max_iter=5,
                                learning_method='online',
                                learning_offset=50.,
                                random_state=0)
t0 = time()
lda.fit(tf)
print("done in %0.3fs." % (time() - t0))

print("\nTopics in LDA model:")
tf_feature_names = tf_vectorizer.get_feature_names()
print_top_words(lda, tf_feature_names, n_top_words)
store_top_words(lda, tf_feature_names, n_top_words)

NameError: name 'comments_en_train' is not defined

In [27]:
val_en = pd.read_excel('validation_en.xlsx')

In [10]:
val_en.Positive.apply(get_lda_topic)

NameError: name 'tf_vectorizer' is not defined

In [191]:
from sklearn.utils import check_random_state
from sklearn.decomposition._online_lda import _dirichlet_expectation_2d
from sklearn.decomposition import NMF, LatentDirichletAllocation
class PTWGuidedLatentDirichletAllocation(LatentDirichletAllocation):

    def __init__(self, ptws=None, *args, **kwargs):
        super(PTWGuidedLatentDirichletAllocation, self).__init__(*args, **kwargs)
        self.ptws = ptws

    def _init_latent_vars(self, n_features):
        """Initialize latent variables."""

        self.random_state_ = check_random_state(self.random_state)
        self.n_batch_iter_ = 1
        self.n_iter_ = 0

        if self.doc_topic_prior is None:
            self.doc_topic_prior_ = 1. / self.n_topics
        else:
            self.doc_topic_prior_ = self.doc_topic_prior

        if self.topic_word_prior is None:
            self.topic_word_prior_ = 1. / self.n_topics
        else:
            self.topic_word_prior_ = self.topic_word_prior

        init_gamma = 100.
        init_var = 1. / init_gamma
        # In the literature, this is called `lambda`
        self.components_ = self.random_state_.gamma(
            init_gamma, init_var, (self.n_topics, n_features))

        # Transform topic values in matrix for prior topic words
        if self.ptws is not None:
            for ptw in self.ptws:
                word_index = ptw[0]
                word_topic_values = ptw[1]
                self.components_[:, word_index] *= word_topic_values

        # In the literature, this is `exp(E[log(beta)])`
        self.exp_dirichlet_component_ = np.exp(
            _dirichlet_expectation_2d(self.components_))

In [101]:
from sklearn.feature_extraction import stop_words
sw = list(stop_words.ENGLISH_STOP_WORDS)
sw.append('game')
sw.append('games')
sw.append('good')
sw.append('great')

In [193]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from __future__ import print_function
from time import time
tf_vectorizer = CountVectorizer(max_df=0.95, min_df=2,
                                ngram_range = (1,3),
                                max_features=10000,
                                stop_words=sw)
t0 = time()
tf = tf_vectorizer.fit_transform(comments_en.cleaned)

In [194]:
tf_vectorizer.vocabulary_['cool']

1414

In [195]:
# List with prior topic words as tuples
# (word index, [topic values])
def prior_dist(n_topic):
    dist = [0.,0.,0.,0.,0.]
    dist[n_topic] = (np.finfo(np.float64).max/4)
    return dist
prior_topic_words = [
    (tf_vectorizer.vocabulary_['crash'],prior_dist(0)),
    (tf_vectorizer.vocabulary_['crashes'],prior_dist(0)),
    (tf_vectorizer.vocabulary_['crashing'],prior_dist(0)),
    (tf_vectorizer.vocabulary_['balance'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['balanced'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['unbalanced'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['overpowered'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['op'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['match'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['unfair'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['prices'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['weapon cost'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['powerful'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['fair'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['hard'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['higher'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['level'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['level'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['buy gem'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['matchmaking'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['beast'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['level 27'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['pay win'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['powered'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['guns cost'],prior_dist(1)),
    (tf_vectorizer.vocabulary_['lost'],prior_dist(2)),
    (tf_vectorizer.vocabulary_['lose'],prior_dist(2)),
    (tf_vectorizer.vocabulary_['trophies'],prior_dist(2)),
    (tf_vectorizer.vocabulary_['losing'],prior_dist(2)),
    (tf_vectorizer.vocabulary_['deleted'],prior_dist(2)),
    (tf_vectorizer.vocabulary_['awesome'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['amazing'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['awesome cool'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['awesome graphic'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good gameplay'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good time'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good job'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['fun love'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['fun great'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['really like'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good best'],prior_dist(3)),
    #(tf_vectorizer.vocabulary_['good graphics'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['best'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['cool'],prior_dist(3)),
    (tf_vectorizer.vocabulary_['bug'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['bugs'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['lag'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['lags'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['lagging'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['update'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['google play'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['fix'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['fix'],prior_dist(0)),
    (tf_vectorizer.vocabulary_['fix bug'],prior_dist(4)),
    (tf_vectorizer.vocabulary_['fix bug'],prior_dist(0)),
    (tf_vectorizer.vocabulary_['google'],prior_dist(4)),
    #(tf_vectorizer.vocabulary_['get ban'],prior_dist(4))
]

# Example (word at index 3000 belongs to topic with index 0)
#prior_topic_words.append(
#    (3000, [(np.finfo(np.float64).max/4),0.,0.,0.,0.])
#)

In [196]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
comments = pd.read_csv('comments_en_cleaned.csv')
comments_en = comments[comments.lang == 'en']
vect = CountVectorizer(ngram_range = (1,1), analyzer = 'word',
                       stop_words = 'english',
                       max_features = 10000,
                       min_df = 2, max_df = 0.95).fit(comments_en.Review)

In [197]:
pw = list(vect.vocabulary_.keys())

In [198]:
def store_top_words(model, feature_names, n_top_words):
    msg = []
    for topic_idx, topic in enumerate(model.components_):
        #message = "Topic #%d: " % topic_idx
        message = " ".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        msg.append(message)
    res = pd.Series(msg)
    res.to_excel('lda_topics.xls')

    
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += "' '".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)
    print()

In [199]:
def make_top_words_dict(model, feature_names, n_top_words):
    res = {}
    kw = []
    for topic_idx, topic in enumerate(model.components_):
        for i in topic.argsort()[:-n_top_words - 1:-1]:
            kw.append(feature_names[i])
    k = 0
    for w in list(set(kw)):
        res[w] = k
        k+=1
    return res

In [200]:
lda = PTWGuidedLatentDirichletAllocation(n_topics=5, max_iter=5,
                                learning_method='online',
                                learning_offset=5.,
                                random_state=0,
                                ptws = prior_topic_words)
t0 = time()
lda.fit(tf)
print("done in %0.3fs." % (time() - t0))

print("\nTopics in LDA model:")
tf_feature_names = tf_vectorizer.get_feature_names()
#print_top_words(lda, tf_feature_names, 200)
#store_top_words(lda, tf_feature_names, 1000)

/home/lsm/anaconda3/lib/python3.6/site-packages/sklearn/decomposition/online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)
/home/lsm/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:38: RuntimeWarning: overflow encountered in multiply


done in 68.648s.

Topics in LDA model:


In [201]:
def get_lda_topic(text):
    cleaned_text = clean_comment(text)
    tf_feats = tf_vectorizer.transform([cleaned_text])
    #return np.argmax(lda.transform(tf_feats)[0])
    return np.argmax(lda.transform(tf_feats)[0])+1

In [202]:
get_lda_topic('this dum gaem crashes every time i launch it')

1

In [203]:
get_lda_topic('tis a great game but those new weapons are so dam op')

1

In [204]:
get_lda_topic('The game glitched and all of my trophies and guns are now lost')

1

In [205]:
get_lda_topic('Cool!')

1

In [206]:
get_lda_topic('This game is haard to control')

1

In [145]:
from sklearn.metrics import classification_report, accuracy_score
def val_score(model):
    class_names = ['Other',
        'Crash',
        'Balance problems',
        'Synchronization',
        'Positive',
        'Bug']    
    val_en = pd.read_excel('validation_en.xlsx')
    y_true = []
    y_pred = []
    for i in range(0,6):
        y_true.append([i]*10)
        y_pred.append(val_en.iloc[:,i].apply(get_lda_topic))
    y_true = np.array(y_true).flatten()
    y_pred = np.array(y_pred).flatten()
    print(classification_report(y_true, y_pred, target_names = class_names))
    print('model accuracy %1.4f'%(accuracy_score(y_true, y_pred)))
    return y_true,y_pred

In [146]:
y_true,y_pred = val_score(None)

                  precision    recall  f1-score   support

           Other       0.00      0.00      0.00        10
           Crash       0.17      1.00      0.29        10
Balance problems       0.00      0.00      0.00        10
 Synchronization       0.00      0.00      0.00        10
        Positive       0.00      0.00      0.00        10
             Bug       0.00      0.00      0.00        10

     avg / total       0.03      0.17      0.05        60

model accuracy 0.1667


/home/lsm/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [124]:
val_en.Bug.apply(get_lda_topic)

NameError: name 'val_en' is not defined

In [281]:
y_true = []
y_pred = []
for i in range(5):
    y_true.append([i]*10)
    y_pred.append(val_en.iloc[:,i].apply(get_lda_topic))
y_true = np.array(y_true).flatten()
y_pred = np.array(y_pred).flatten()

In [282]:
class_names = [#'unknown',
    'Crash',
    'Balance problems',
    'Synchronization',
    'Positive',
    'Bug']
print(classification_report(y_true, y_pred, target_names = class_names))

                  precision    recall  f1-score   support

           Crash       0.35      0.60      0.44        10
Balance problems       0.62      0.50      0.56        10
 Synchronization       1.00      0.50      0.67        10
        Positive       0.60      0.60      0.60        10
             Bug       0.60      0.60      0.60        10

     avg / total       0.64      0.56      0.57        50



In [283]:
comments_en['label'] = comments_en.Review.apply(get_lda_topic)

/home/lsm/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [284]:
comments_en.label.value_counts()

0    11072
3     5812
4     1302
1     1102
2      494
Name: label, dtype: int64

In [320]:
tw_dict = make_top_words_dict(lda, tf_feature_names, 1000)

In [329]:
labeled = pd.read_excel('manual_labels.xlsx')

In [354]:
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression, RidgeClassifier
from sklearn.naive_bayes import BernoulliNB, MultinomialNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier
from sklearn.multiclass import OneVsRestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

In [355]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
vect = CountVectorizer(ngram_range = (1,3), analyzer = 'word', stop_words = sw,
                       vocabulary = tw_dict, min_df = 2, max_df = 0.95).fit(labeled.Review)
feats = vect.transform(labeled.Review)
labels = labeled.label

In [356]:
def eval_model(y_train,y_test,y_train_pred,y_test_pred):
    class_names = ['unknown',
        'Crash',
        'Balance problems',
        'Synchronization',
        'Positive',
        'Bug']
    print('train scores\n')
    print(classification_report(y_train, y_train_pred, target_names = class_names))
    print('test scores\n')
    print(classification_report(y_test, y_test_pred, target_names = class_names))

In [357]:
X_train, X_test, y_train, y_test = train_test_split(feats, labels, test_size=0.2)

In [371]:
m = RidgeClassifier(class_weight = 'balanced').fit(X_train, y_train)
y_train_pred = m.predict(X_train)
y_test_pred = m.predict(X_test)
eval_model(y_train,y_test,y_train_pred,y_test_pred)

ValueError: Floating-point under-/overflow occurred at epoch #691. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.

Exception ignored in: 'sklearn.linear_model.sag_fast.raise_infinite_error'
ValueError: Floating-point under-/overflow occurred at epoch #691. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.


ValueError: Floating-point under-/overflow occurred at epoch #691. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.

Exception ignored in: 'sklearn.linear_model.sag_fast.raise_infinite_error'
ValueError: Floating-point under-/overflow occurred at epoch #691. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.


ValueError: Floating-point under-/overflow occurred at epoch #691. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.

...

ValueError: Floating-point under-/overflow occurred at epoch #678. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.

Exception ignored in: 'sklearn.linear_model.sag_fast.raise_infinite_error'
ValueError: Floating-point under-/overflow occurred at epoch #678. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.


ValueError: Floating-point under-/overflow occurred at epoch #678. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.

Exception ignored in: 'sklearn.linear_model.sag_fast.raise_infinite_error'
ValueError: Floating-point under-/overflow occurred at epoch #678. Lowering the step_size or scaling the input data with StandardScaler or MinMaxScaler might help.
/home/lsm/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


train scores

                  precision    recall  f1-score   support

         unknown       0.06      1.00      0.11        47
           Crash       0.00      0.00      0.00         4
Balance problems       0.00      0.00      0.00       157
 Synchronization       0.00      0.00      0.00        24
        Positive       0.00      0.00      0.00       503
             Bug       0.00      0.00      0.00        65

     avg / total       0.00      0.06      0.01       800

test scores

                  precision    recall  f1-score   support

         unknown       0.07      1.00      0.12        13
           Crash       0.00      0.00      0.00         4
Balance problems       0.00      0.00      0.00        46
 Synchronization       0.00      0.00      0.00         7
        Positive       0.00      0.00      0.00       121
             Bug       0.00      0.00      0.00         9

     avg / total       0.00      0.07      0.01       200



In [364]:
def eval_classifier(input_text,model = m):
    feats = vect.transform([input_text])
    class_names = [#'unknown',
        'Crash',
        'Balance problems',
        'Synchronization',
        'Positive',
        'Bug']
    prediction = model.predict(feats)
    #print(class_names[prediction[0]])
    return prediction[0]

In [389]:
val_en.Crash.apply(eval_classifier)

0    4
1    4
2    5
3    2
4    5
5    5
6    4
7    4
8    4
9    4
Name: Crash, dtype: int64

In [386]:
def eval_model(y_train,y_test,y_train_pred,y_test_pred):
    class_names = ['unknown',
        'Crash',
        'Balance problems',
        'Synchronization',
        'Positive',
        'Bug']
    print('train scores\n')
    print(classification_report(y_train, y_train_pred, target_names = class_names))
    print('test scores\n')
    print(classification_report(y_test, y_test_pred, target_names = class_names))

In [387]:
y_true = []
y_pred = []
for i in range(5):
    y_true.append([i]*10)
    y_pred.append(val_en.iloc[:,i].apply(eval_classifier))
y_true = np.array(y_true).flatten()
y_pred = np.array(y_pred).flatten()

In [388]:
class_names = ['unknown',
    'Crash',
    'Balance problems',
    'Synchronization',
    'Positive',
    'Bug']
print(classification_report(y_true, y_pred, target_names = class_names))

                  precision    recall  f1-score   support

         unknown       0.00      0.00      0.00        10
           Crash       0.00      0.00      0.00        10
Balance problems       0.29      0.70      0.41        10
 Synchronization       0.00      0.00      0.00        10
        Positive       0.21      0.40      0.28        10
             Bug       0.00      0.00      0.00         0

     avg / total       0.10      0.22      0.14        50



/home/lsm/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/lsm/anaconda3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
